In [1]:
# !pip install sentence_transformers

# import json
# from tqdm import tqdm
# from sentence_transformers import CrossEncoder


In [2]:
# # Load evidence snippets
# with open('/kaggle/input/claimdecomp3/corpus_evidence_unified.json', 'r') as f:
#     evidence_corpus = json.load(f)

# type(evidence_corpus)

In [3]:
# import csv
# decomposed_questions = []
# with open('/kaggle/input/claimdecomp3/claim_decomp_train', 'r', newline='') as file:
#     reader = csv.reader(file)
#     for row in reader:
#         decomposed_questions.append(row)
        

In [4]:
# import torch
# device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
# print(f"Using device: {device}")

In [5]:
# def split_questions(questions_str):
#     questions = [q.strip() for q in questions_str.split('?') if q.strip()]
#     questions = [q + '?' for q in questions if not q.endswith('?')]
#     return questions

In [6]:
# re_ranker = CrossEncoder('cross-encoder/ms-marco-MiniLM-L-6-v2')
# re_ranker.model.to(device)

# def rerank_snippets(question, evidence_list, top_k=5):
#     pairs = [[question, snippet] for snippet in evidence_list if snippet.strip()]  # Remove empty or whitespace-only snippets
#     if not pairs:
#         return ""
#     scores = re_ranker.predict(pairs)
#     ranked_snippets = [snippet for _, snippet in sorted(zip(scores, evidence_list), reverse=True)]
# #     print(ranked_snippets)
#     return (ranked_snippets[:top_k]) 

In [7]:
# nli_data = []

# for idx, item in enumerate(tqdm(decomposed_questions, desc="Processing claims")):
#     questions = decomposed_questions
#     evidence_list = evidence_snippets[idx]['evidence_snippet_list']  # Retrieve evidence list for the claim
    
#     combined_snippets = set()
#     for question in questions:
#         top_snippets = rerank_snippets(question, evidence_list)
#         combined_snippets.update(top_snippets)
    
#     combined_evidence = ' '.join(combined_snippets)
#     nli_input = {
#         'decomposed_questions': questions_str,
#         'evidence': combined_evidence
#     }
#     nli_data.append(nli_input)

In [8]:
# # Save the final NLI input data
# with open('/kaggle/working/nli_val_decomposed_reranked.json', 'w') as f:
#     json.dump(nli_data, f)

# Rerank stuff


In [9]:
!pip install rank-bm25
!pip install sentence_transformers
!pip install nltk
import json
from rank_bm25 import BM25Okapi
from tqdm import tqdm
from sentence_transformers import CrossEncoder
import nltk
nltk.download('punkt')

from nltk.tokenize import sent_tokenize

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.1/227.1 kB 8.7 MB/s eta 0:00:00


/opt/conda/lib/python3.10/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:11: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange
2024-06-10 17:09:04.285440: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-06-10 17:09:04.285569: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-06-10 17:09:04.423900: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


[nltk_data] Downloading package punkt to /usr/share/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [10]:
import json
with open('/kaggle/input/claimdecomp3/corpus_evidence_unified.json', 'r') as f:
    evidence_corpus = json.load(f)



In [11]:
# import os
# os.chdir("/kaggle/input/claimdecomp2")
# os.listdir() # to see files in this directory

In [12]:
import csv
claims = []
with open('/kaggle/input/claimdecomp3/claim_decomp_val', 'r', newline='') as file:
    reader = csv.reader(file)
    for row in reader:
        claims.append(row)
        
claims = claims[3000:3500]
# claims = claims[:3]
        

In [13]:
corpus = [evidence for evidence in tqdm(evidence_corpus.values())]
tokenized_corpus = [doc.split() for doc in corpus]

100%|██████████| 423320/423320 [00:00<00:00, 2921120.14it/s]


In [14]:
bm25 = BM25Okapi(tokenized_corpus)

In [15]:
def retrieve_evidence(claim, k=100):
    tokenized_claim = claim.split()
    scores = bm25.get_scores(tokenized_claim)
    top_k_indices = scores.argsort()[-k:][::-1]
    top_k_documents = [corpus[idx] for idx in top_k_indices]
    return top_k_documents

In [16]:
import torch
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(f"Using device: {device}")

Using device: cpu


In [17]:
# re_ranker = CrossEncoder('cross-encoder/ms-marco-MiniLM-L-6-v2')

# re_ranker.model.to(device)

# def rerank_snippets(claim, evidence_list, top_k=5):
#     pairs = [[claim, snippet] for snippet in evidence_list if snippet.strip()]  # Remove empty or whitespace-only snippets
#     if not pairs:
#         return ""
#     scores = re_ranker.predict(pairs)
#     ranked_snippets = [snippet for _, snippet in sorted(zip(scores, evidence_list), reverse=True)]
#     return ' '.join(ranked_snippets[:top_k]) 

In [18]:
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np

model = SentenceTransformer('sentence-transformers/all-MiniLM-l6-v2')


def get_top_k_evidences(model, claim, evidence, k):
    evidence_emb = model.encode(evidence)
    top_k_results = []

    claim_emb = model.encode(claim)
    text_sims = cosine_similarity(evidence_emb, [claim_emb]).tolist()
    results_sims = zip(range(len(text_sims)), text_sims)
    sorted_similarities = sorted(results_sims, key=lambda x: x[1], reverse=True)

    top_k_evidence = []
    for idx, item in sorted_similarities[:k]:
        top_k_evidence.append(evidence[idx])

    return top_k_evidence

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.7k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

/opt/conda/lib/python3.10/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


...

tokenizer_config.json:   0%|          | 0.00/350 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [19]:
total_evidence = []
nli_data = []

k = 7

for claimdecomps in tqdm(claims):
    cur_evidences = []
    cur_nli_data = []
    for claim_decomp in claimdecomps:
        claim_text = claim_decomp
        evidence_list = retrieve_evidence(claim_text)

        evidence_input = {
            'claim': claim_text,
            'evidence_snippet_list': evidence_list
        }

        reranked_evidence = get_top_k_evidences(model, claim_text, evidence_list, k)
        nli_input = {
            'claim': claim_text,
            'evidence': reranked_evidence
        }
        cur_evidences.append(evidence_input)
        cur_nli_data.append(nli_input)
        
        
    total_evidence.append(cur_evidences)
    nli_data.append(cur_nli_data)


  0%|          | 0/84 [00:00<?, ?it/s]

Batches:   0%|          | 0/4 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/4 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/4 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/4 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

100%|██████████| 84/84 [27:47<00:00, 19.85s/it]


In [20]:
cur = nli_data[0][0]['evidence']
print(type(cur))
print(len(cur))
print(cur)

<class 'list'>
7
['7 avr. 2020  the researchers found that the virus lasted up to three days on plastic and stainless steel  a shorter time than the results in the the lancet ...', '2022-01-04  reproductive system and breast disorders (ir: 2.00 vs 1.25) with 55 ... in the time between last vaccine dose and onset of symptoms. despite ...', 'drastic decrease in life expectancy occurred by about - 1.75. this occurred only in some states of europe because of the covid-19 pandemic. according', 'the length of time between exposure to the virus and the development of symptoms (incubation period) is between 2 and 21 days, and usually between 4 and 10 days ...', 'among 36,523 participants who had no evidence of existing or prior sars-cov-2 infection by the time of the immunizations, there were 170 cases of covid-19 observed with onset at least 7 days after the second dose; 8 cases occurred in vaccine recipients, and 162 in placebo recipients, corresponding to 95.0% vaccine efficacy (95% credibl

In [21]:
with open('/kaggle/working/nli_llmclaimdecomp_input_val_reranktop7_500_fourth.json', 'w') as f:
    json.dump(nli_data, f)

In [22]:
with open('/kaggle/working/nli_llmclaimdecomp_input_val_evidence_withoutrerank_500_fourth.json', 'w') as f:
    json.dump(total_evidence, f)